In [1]:
import sys
import os
import SimpleITK
import numpy
import matplotlib.pyplot
import subprocess
import json
import re
import config
import getData
import analysis

sys.path.append(os.path.join(os.path.expanduser('~'),'software','src','nixSuite','wrapper'))
import nixWrapper
nixWrapper.loadLibrary('labkeyInterface')
import labkeyInterface
import labkeyFileBrowser
import labkeyDatabaseBrowser

def connect(server,f):
    net=labkeyInterface.labkeyInterface()
    fconfig=os.path.join(os.path.expanduser('~'),'.labkey','{}.json'.format(server))
    net.init(fconfig)
    net.getCSRF()
    return f(net)

def connectDB(server):
    return connect(server,labkeyDatabaseBrowser.labkeyDB)

def connectFB(server):
    return connect(server,labkeyFileBrowser.labkeyFileBrowser)



remoteSourcesURL https://git0.fmf.uni-lj.si/studen/nixSuite/raw/master/remoteResources/resources.json
{'labkeyInterface': {'url': 'https://git0.fmf.uni-lj.si/studen/labkeyInterface/archive/master.zip', 'branch': 'master', 'modules': []}, 'irAEMM': {'url': 'https://git0.fmf.uni-lj.si/studen/iraemm/archive/master.zip', 'branch': 'master', 'modules': ['iraemmBrowser']}, 'SlicerLabkeyExtension': {'url': 'https://git0.fmf.uni-lj.si/studen/SlicerLabkeyExtension/archive/SlicerExtensionIndex.zip', 'branch': 'SlicerExtensionIndex', 'modules': ['labkeyBrowser']}, 'limfomiPET': {'url': 'https://git0.fmf.uni-lj.si/studen/limfomiPET/archive/master.zip', 'branch': 'master', 'modules': ['imageBrowser']}, 'parseConfig': {'url': 'https://git0.fmf.uni-lj.si/studen/parseConfig/archive/master.zip', 'branch': 'master', 'modules': []}, 'orthancInterface': {'url': 'https://git0.fmf.uni-lj.si/studen/orthancInterface/archive/master.zip', 'branch': 'master', 'modules': []}}


In [2]:
#setup
fsetup='../template/cardiacSPECT.json'
with open(fsetup,'r') as f:
    setup=json.load(f)

db=connectDB('merlin')
fb=connectFB('merlin')
    

    


In [ ]:
#doAnalysis

#fill the Imaging1 fields, for multiple visits, change sequence number


#0.) convert to NRRD 
# ~/software/src/SlicerLabkeyExtenstion/slicerScripts/runSlicer.sh convertToNRRD.py ../template/cardiacSPECT.json)

#this is not performed at vangogh, use Analysis on merlin, convertNRRD.py with cardiacSPECT.json

#1.) downloadFiles

#getData.downloadPatientFiles(db,fb,setup)
#this should also be done at vangogh... Figuring out how

#2.) generate (c-cluster) centers

#setup the analysis (class sizes, number of realizations)
nclass=[10,20,30]
#nclass=[10]
nr=20
#nr=1

#takes multiple hours for nr=20, nclass=[10,20,30]
#runs matlab - maybe the first time licensing will be checked and error will be returned
#just run once
#analysis.calculateCenters(db,setup,nclass,nr)

#3.) now do analysis - global gets the average IVF fit (see point one of the slides for both branches of analysis)
#this again takes multiple hours for four images
#from what I see this could be shortend (since only global parameters are sought)
#analysis.doAnalysis(db,setup,nclass,nr,'global')

#4.) do cluster analysis (bullets two and three under ML analysis)
#analysis.doAnalysis(db,setup,nclass,nr,'IVF')

#5.) sort out the segmentation points -> segmentation.ipynb and generate Segmentation.txt files read by pixelAnalysis

#6.) run doPixelAnalysisIVF to calculate parameters from locations
sigma2=[0.1,1,4]
#analysis.doPixelAnalysis(db,setup,sigma2)

#7.) store summary to database
na=3
s2=0.1
#summary=analysis.fullSummary(db,setup,nclass,nr,s2,na)
#analysis.storeSummary(db,setup,summary,s2,na)

summaryIVF=analysis.summaryPixelIVF(db,setup,sigma2)
analysis.storeIVF(db,setup,summaryIVF)

#8.) Plot regions through chart wizard on labkey, see also Summary R Report for error-plots on multi-class analysis
